In [410]:
import pandas as pd
import datetime as dt
import geopandas as gpd
import folium
import branca.colormap as cm
from folium.plugins import TimestampedGeoJson
#from folium.features import GeoJsonPopup, GeoJsonTooltip

In [411]:
#Reading json file
bikedata=pd.read_json('/Users/alexanderlindell/Documents/Programmering /Python/Sthlm-EbikeVis-/stations2-copy.json')

In [412]:
#Dict with column names 
df={'date':[],'station':[],'occupancy':[],'capacity':[],'long':[],'lat':[]}
df

{'date': [],
 'station': [],
 'occupancy': [],
 'capacity': [],
 'long': [],
 'lat': []}

In [413]:
for _,row in bikedata.iterrows():
    for item in row:
        for cell in item['data']: 
            #print(cell['date'])
            df['occupancy'].append(cell['occupancy'])
            df['capacity'].append(cell['capacity'])
            df['date'].append(cell['date'])
            df['station'].append(item['id'])
            #print(cell['date'],item['coord']['lon'],item['coord']['lat'])
            df['long'].append(item['coord']['lon'])
            df['lat'].append(item['coord']['lat'])


In [414]:
#Setting up dataframe from dict and fix formatting on timestamp. 
data=pd.DataFrame.from_dict(df)
data['date']= pd.to_datetime(df['date'],unit='s')
data['date']=data['date'].dt.strftime('%Y-%m-%dT%H:%M:%S')
data=data.sort_values(by='date')
data

date                               station  occupancy  \
0      2022-05-19T21:30:00  003b4566-1a1d-4aa5-9b2c-35972a0ac219          4   
1584   2022-05-19T21:30:00  28ef3974-af0f-4b72-913b-1138d78e1bb5          0   
8928   2022-05-19T21:30:00  ddad0994-42a6-4e6a-bf67-0ff3925d150b          5   
1728   2022-05-19T21:30:00  2eae80d8-9009-4724-b1bd-c8506c433ed1          0   
8784   2022-05-19T21:30:00  d9d92b3d-5846-4df0-bb76-5da15821c62a          6   
...                    ...                                   ...        ...   
7343   2022-05-21T09:24:04  90beb6ce-1e2b-4586-9514-4cd9ef0aff7c          1   
7487   2022-05-21T09:24:04  a679c4c4-01e6-4c44-9cb7-13b2c34ecbc2          0   
7631   2022-05-21T09:24:04  af8c27f2-b431-42cc-b659-46ae4922097f          2   
5183   2022-05-21T09:24:04  691d4e1c-0620-47ee-a5cd-901df077e3d0          1   
10655  2022-05-21T09:24:04  ffb197fc-9534-42eb-8090-6ff4ccecf7f3          0   

       capacity       long        lat  
0            12  17.993884  59.324599  
1584         16  18.041121  59.337787  
8928         24  18.073418  59.333171  
1728         30  18.051866  59.335261  
8784         24  18.077731  59.298585  
...         ...        ...        ...  
7343         10  18.098270  59.308706  
7487         11  18.091972  59.342983  
7631         12  18.018387  59.328284  
5183         14  18.051044  59.343040  
10655        16  18.070286  59.341596  

[10656 rows x 6 columns]

In [415]:
#Setting the status colors for occupancy dependent on capacity.
colorbar = cm.StepColormap(colors=['#15B01A','#FFA500','#FF7F00','#FF4500','#8B0000'], vmin=0,vmax=1)
data['color']=list(colorbar(x/y) for x,y in zip(data['occupancy'],data['capacity']))

In [416]:
#Adjusting size of markers. 
def setradius(size):
    radius=4 if (size*0.2) < 4 else (size*0.2)
    return(radius)

In [417]:
""" features = []    
for _, row in data.iterrows():
    feature = {
        'type': 'Feature',
        'geometry': {
            'type':'Point', 
            'coordinates':[row['long'],row['lat']]
        },
        'properties': {
            'time': row['date'],
            'popup': 1,
            'style': {'color' : ''},
            'icon': 'circle',
            'iconstyle':{
                'fillColor': row['color'],
                'fillOpacity': 1,
                'stroke': 'true',
                'radius': setradius(row['capacity'])
            }
        }
    }
    features.append(feature) """

" features = []    \nfor _, row in data.iterrows():\n    feature = {\n        'type': 'Feature',\n        'geometry': {\n            'type':'Point', \n            'coordinates':[row['long'],row['lat']]\n        },\n        'properties': {\n            'time': row['date'],\n            'popup': 1,\n            'style': {'color' : ''},\n            'icon': 'circle',\n            'iconstyle':{\n                'fillColor': row['color'],\n                'fillOpacity': 1,\n                'stroke': 'true',\n                'radius': setradius(row['capacity'])\n            }\n        }\n    }\n    features.append(feature) "

In [453]:
features = [{'type': 'Feature',
            'geometry': {'type':'Point', 'coordinates':[row['long'],row['lat']]},
            'properties': {'time': row['date'],
                           'popup':('Occupancy: '+str(row['occupancy'])+'/'+str(row['capacity'])),
                           'style': {'color' : ''},
                           'icon': 'circle',
                           'iconstyle':{'fillColor': row['color'],
                                        'fillOpacity': 1,
                                        'stroke': 'true',
                                        'radius': setradius(row['capacity'])}}
            } for _,row in data.iterrows()]

In [454]:
map = folium.Map(location = [59.32760990395156, 18.06760960579676], tiles='Stamen Toner' , zoom_start = 12)
TimestampedGeoJson( features,
                            add_last_point = True,
                           period='PT10M',
                           loop_button=True,
                           time_slider_drag_update=True,
                           transition_time = 100,
                           
                            ).add_to(map)
map.add_child(colorbar)
map


In [420]:
map.save('SthlmEBikeVis.html')